In [1]:
import sys
sys.path.append('../code')
from init_mooc_nb import *
init_notebook()

Populated the namespace with:
np, matplotlib, kwant, holoviews, init_notebook, SimpleNamespace, pprint_matrix, scientific_number, pretty_fmt_complex, plt, pf, display_html
from code/edx_components:
MoocVideo, PreprintReference, MoocDiscussion, MoocCheckboxesAssessment, MoocMultipleChoiceAssessment, MoocPeerAssessment, MoocSelfAssessment
from code/functions:
spectrum, hamiltonian_array, h_k, pauli
Using kwant 1.3.2 and holoviews 1.9.5+g39fe834be
Executed on 2018-04-13 at 00:38:47.248136.


## Preamble Code

In [2]:
import sys
sys.path.append('../code')
from init_mooc_nb import *
init_notebook()

%opts Layout [sublabel_format='' aspect_weight=1 figure_size=(100) vspace=0.4]
%output size = 150

randn = np.random.randn

alphas = np.linspace(0, 1, 1000)

dims = SimpleNamespace(E=holoviews.Dimension(r'$E$'),
                       alpha=holoviews.Dimension(r'$\alpha$'),
                       Q=holoviews.Dimension(r'$Q$'),
                       Q_BdG=holoviews.Dimension(r'$Q_{BdG}$'))

def make_random_real_ham(N):
    H = randn(N, N)
    H += H.T
    return H / 2


def make_cons_ham(N):
    H = np.kron(pauli.s0, randn(N, N)) + np.kron(pauli.sz, randn(N, N))
    H += H.T.conj()
    return H / 2


def make_random_ham(N):
    H = randn(N, N) + 1j * randn(N, N)
    H += H.T.conj()
    return H / 2


def make_random_symplectic_ham(N):
    if N % 2:
        raise ValueError('Matrix dimension should be a multiple of 2')
    sy = np.kron(np.eye(N // 2), np.array([[0, -1j], [1j, 0]]))
    h = randn(N, N) + 1j * randn(N, N)
    h += h.T.conj()
    Th = sy @ h.conj() @ sy
    return (h + Th) / 4


def make_chiral_ham(N):
    temp1 = randn(N, N) + 1j * randn(N, N)
    temp2 = randn(N, N) + 1j * randn(N, N)    
    H = np.kron(pauli.sx, temp1) + np.kron(pauli.sy, temp2)
    H += H.T.conj()
    return H / 2


def make_BdG_ham(N):
    # This is antisymmetric basis
    H = 1j * randn(2*N, 2*N)
    H += H.T.conj()
    return H / 2


def energies(alpha, H0, H1):
    H = (1 - alpha) * H0 + alpha * H1
    return np.linalg.eigvalsh(H)


def find_spectrum(alphas, H0, H1):
    spectrum = [energies(a, H0, H1) for a in alphas]
    return np.array(spectrum)


def find_Q(spectrum):
    """Finds the number of bands that are under zero energy.

    Parameters:
    -----------
    spectrum : numpy array
        Array that contains the energies levels for every alpha.

    Returns:
    --------
    Q : list
        Number of bands under zero energy.
    """
    return [len(s[s<0]) for s in spectrum]


def plot_hamiltonian_spectrum(alphas, spectrum, E_range=(-4, 4)):
    """Function that plots a spectrum for a range of alphas.

    Parameters:
    -----------
    alphas : numpy array
        Range of alphas for which the energies are calculated.
    spectrum : numpy array
        Array that contains the energies levels for every alpha.
    E_range : tuple
        The upper and lower limit of the y-dimension.

    Returns:
    --------
    plot : holoviews.Path object
        Plot of alphas vs. spectrum.
    """
    E_min, E_max = E_range
    plot = holoviews.Path((alphas, spectrum), kdims=[dims.alpha, dims.E])[:, E_min:E_max] * holoviews.HLine(0)
    return plot(plot={'xticks':[0, 0.5, 1], 'yticks':[E_min, 0, E_max]})


def plot_Q(alphas, Q, Q_range, Q_dim=dims.Q):
    """Function that plots value of Q for a range of alphas.

    Parameters:
    -----------
    alphas : numpy array
        Range of alphas for which the energies are calculated.
    Q : numpy array
        Vector that contains the value of Q for every alpha.
    Q_range : tuple
        The upper and lower limit of the y-dimension.

    Returns:
    --------
    plot : holoviews.Path object
        Plot of alphas vs. Q.
    """
    Q_min, Q_max = Q_range
    Q_mid = (Q_max + Q_min) / 2
    plot = holoviews.Area((alphas, Q), kdims=[dims.alpha], vdims=[Q_dim])[:, Q_min:Q_max](style={'alpha': 0.4})
    plot *= holoviews.Curve((alphas, Q), kdims=[dims.alpha], vdims=[Q_dim])[:, Q_min:Q_max]
    return plot(plot={'xticks':[0, 0.5, 1], 'yticks':[Q_min, Q_mid, Q_max], 'aspect':4})

Populated the namespace with:
np, matplotlib, kwant, holoviews, init_notebook, SimpleNamespace, pprint_matrix, scientific_number, pretty_fmt_complex, plt, pf, display_html
from code/edx_components:
MoocVideo, PreprintReference, MoocDiscussion, MoocCheckboxesAssessment, MoocMultipleChoiceAssessment, MoocPeerAssessment, MoocSelfAssessment
from code/functions:
spectrum, hamiltonian_array, h_k, pauli
Using kwant 1.3.2 and holoviews 1.9.5+g39fe834be
Executed on 2018-04-13 at 00:38:48.199958.


In [3]:
%%opts Overlay [yticks=[-1, 0, 1]]

def find_pfaffian(alphas, H0, H1):
    """Function caculates the Pfaffian for a Hamiltonian.

    Parameters:
    -----------
    alphas : numpy array
        Range of alphas for which the energies are calculated.
    H0 : numpy array
        Hamiltonian, same size as H1.
    H1 : numpy array
        Hamiltonian, same size as H0.
        
    Returns:
    --------
    pfaffians : numpy array
        Pfaffians for each alpha.
    """
    def H(alpha):
        return (1 - alpha) * H0 + alpha * H1
    pfaffians = [np.sign(np.real(pf.pfaffian(1j*H(a)))) for a in alphas]
    return np.array(pfaffians)

pfaffian = find_pfaffian(alphas, H0, H1)
(plot_hamiltonian_spectrum(alphas, spectrum, [-1.5, 1.5]) + plot_Q(alphas, pfaffian, [-1.5, 1.5], dims.Q_BdG)).cols(1)

NameError: name 'H0' is not defined

# Simulations: what about other symmetries

So you've made it through the content of the first week. Congratulations!

Now let's get our hands dirty. 

Let's begin by grabbing the notebooks of this week and the extra code we use to run these notebooks over [here](http://tiny.cc/topocm_smc). (Click the [i] button to the left of the folder that you want to copy.)

You need to copy the `code` folder and the `w1_topointro` folder. Let's look into what's inside.


## First task: combination of particle-hole and time-reversal symmetries

Look at the notebook about topology of zero-dimensional systems, and see how we generate Hamiltonians with a spinful time-reversal symmetry

$$
H = \sigma_y H^* \sigma_y.
$$

Now try to add this time reversal symmetry to a Hamiltonian which also has particle-hole symmetry. It is easiest to do in the basis where particle-hole symmetry has the form $H = -H^*$.
What do you think will happen? What will the extra symmetry do to the topological invariant?
Test your guess by plotting the spectrum and calculating the Pfaffian invariant.




### What do you think will happen?
The addition of spinful time-reversal symmetry will apply Kramer's degeneracy to the Hamiltonian's (ie. all energy levels will be doubly degenerate. Whereas previously it was possible to have zero energy crossings of particle-hole anti-symmetric pairs the symmetry enforces that each energy level be doubly degenerate (any zero-crossing causes a change of $\pm2$ and the Energy spectrum must be symmetric with regards to reflection around $E=0$

In [4]:
 
N = 8
H0 = make_random_symplectic_ham(N=N)
H1 = make_random_symplectic_ham(N=N)
spectrum = find_spectrum(alphas, H0, H1)
plot_hamiltonian_spectrum(alphas, spectrum)

:Overlay
   .Path.I  :Path   [$\alpha$,$E$]
   .HLine.I :HLine   [x,y]

### What will the extra symmetry do to the topological invariant?
The addition of the Time-reversal symmettry will cause the pfaffian to become invariant with respect to a smooth transition between Hamiltonians. This is a result of Kramer's degeneracy swapping the sign of 

### Test your guess by plotting the spectrum and calculating the Pfaffian invariant.

In [5]:
def make_random_symplectic_ham(N):
    if N % 2:
        raise ValueError('Matrix dimension should be a multiple of 2')
    sy = np.kron(np.eye(N // 2), np.array([[0, -1j], [1j, 0]]))
    h = randn(N, N) + 1j * randn(N, N)
    h += h.T.conj()
    Th = sy @ h.conj() @ sy
    return (h + Th) / 4



def make_BdG_ham(N):
    # This is antisymmetric basis
    H = 1j * randn(2*N, 2*N)
    H += H.T.conj()
    return H / 2


def make_time_reversed_particle_hole(N=None,bdg=None):
    if bdg is not None:
        N = bdg.shape[0]
    else:
        bdg = make_BdG_ham(N//2)
    if N % 2:
        raise ValueError('Matrix dimension should be a multiple of 2')
    sy = np.kron(np.eye(N // 2), np.array([[0, -1j], [1j, 0]]))
    h = bdg
    h += h.T.conj()
    Th = sy @ h.conj() @ sy
    return (h + Th) / 4
    
    
    

In [6]:
N = 4
bdg = make_BdG_ham(N)
pprint_matrix(bdg)

In [7]:
time_reversed_bdg = make_time_reversed_particle_hole(bdg=bdg)
pprint_matrix(time_reversed_bdg)

In [8]:
N = 32
H0 = make_time_reversed_particle_hole(N=N)
H1 = make_time_reversed_particle_hole(N=N)
spectrum = find_spectrum(alphas, H0, H1)
pfaffian = find_pfaffian(alphas, H0, H1)
(plot_hamiltonian_spectrum(alphas, spectrum, [-1.5, 1.5]) + plot_Q(alphas, pfaffian, [-1.5, 1.5], dims.Q_BdG)).cols(1)

:Layout
   .Overlay.I  :Overlay
      .Path.I  :Path   [$\alpha$,$E$]
      .HLine.I :HLine   [x,y]
   .Overlay.II :Overlay
      .Area.I  :Area   [$\alpha$]   ($Q_{BdG}$)
      .Curve.I :Curve   [$\alpha$]   ($Q_{BdG}$)

## Second task: Su-Schrieffer-Heeger (SSH) model

Similar to the Kitaev chain, the SSH model is simple a one-dimensional model where you can see all the essential aspects of topological systems. Unlike the Kitaev chain it does correspond to a physical system: electrons in a polyacetylene chain.

Here's such a chain:

![](figures/polyacetylene.png)

Due to the dimerization of the chain the unit cell has two atoms and the hoppings have alternating strengths $t_1$ and $t_2$, so that the Hamiltonian is
$$H = \sum_{n=1}^N t_1 \left|2n-1\right\rangle\left\langle 2n\right|+t_2 \left|2n\right\rangle \left\langle 2n+1\right| + \textrm{h.c}$$

We can choose to start a unit cell from an even-numbered site, so $t_1$ becomes intra-cell hopping and $t_2$ inter-cell hopping.


Now get the notebook with the Kitaev chain and transform a Kitaev chain into an SSH chain.

Now repeat the calculations we've done with Majoranas using SSH chain. Keep $t_1 = 1$ and vary $t_2$.
You should see something very similar to what you saw with the Kitaev chain.

As you can guess, this is because the chain is topological.
Think for a moment: what kind of symmetry protects the states at the edges of the chain.
*(Hint: you did encounter this symmetry in our course.)*

The particle-hole symmetry, is a consequence of a mathematical transformation, and cannot be broken.
The symmetry protecting the SSH chain, however, can be broken.
Test your guess about the protecting symmetry by adding to your chain a term which breaks this symmetry and checking what it does to the spectrum of a finite chain and to its dispersion (especially as chain goes through a phase transition).

### Kitaev Chain Code 

In [41]:
import sys
sys.path.append('../code')
#from init_mooc_nb import *
#init_notebook()

%output size=150
dims = SimpleNamespace(E_t=holoviews.Dimension(r'$E/t$'),
                       mu_t=holoviews.Dimension(r'$\mu/t$'),
                       lambda_=holoviews.Dimension(r'$\lambda$'),
                       x=holoviews.Dimension(r'$x$'),
                       k=holoviews.Dimension(r'$k$'),
                       amplitude=holoviews.Dimension(r'$|u|^2 + |v|^2$'))

holoviews.core.dimension.title_format = ''

def kitaev_chain(L=None, periodic=False):
    lat = kwant.lattice.chain()

    if L is None:
        syst = kwant.Builder(kwant.TranslationalSymmetry((-1,)))
        L = 1
    else:
        syst = kwant.Builder()

    # transformation to antisymmetric basis
    U = np.array([[1.0, 1.0], [1.j, -1.j]]) / np.sqrt(2)

    def onsite(onsite, p): 
        return - p.mu * U @ pauli.sz @ U.T.conj()
    
    for x in range(L):
        syst[lat(x)] = onsite

    def hop(site1, site2, p):
        return U @ (-p.t * pauli.sz - 1j * p.delta * pauli.sy) @ U.T.conj()
    
    syst[kwant.HoppingKind((1,), lat)] = hop

    if periodic:
        def last_hop(site1, site2, p):
            return hop(site1, site2, p) * (1 - 2 * p.lambda_)
        
        syst[lat(0), lat(L - 1)] = last_hop
    return syst


def bandstructure(mu, delta=1, t=1, Dirac_cone="Hide", show_pf=False):
    syst = kitaev_chain(None)
    p = SimpleNamespace(t=t, delta=delta, mu=mu)
    plot = holoviews.Overlay([spectrum(syst, p, ydim="$E/T$", xdim='$k$')][-4:4])
    h_1 = h_k(syst, p, 0)
    h_2 = h_k(syst, p, np.pi)
    pfaffians = [find_pfaffian(h_1), find_pfaffian(h_2)]
    
    if show_pf:
        signs = [('>' if pf > 0 else '<') for pf in pfaffians]
        title = "$\mu = {mu} t$, Pf$(iH_{{k=0}}) {sign1} 0$, Pf$(iH_{{k=\pi}}) {sign2} 0$"
        title = title.format(mu=mu, sign1=signs[0], sign2=signs[1])
        plot *= holoviews.VLine(0) * holoviews.VLine(-np.pi)
    else:
        if pfaffians[0] * pfaffians[1] < 0:
            title = "$\mu = {mu} t$, topological ".format(mu=mu)
        else:
            title = "$\mu = {mu} t$, trivial ".format(mu=mu)
        
    if Dirac_cone == "Show":
        ks = np.linspace(-np.pi, np.pi)
        ec = np.sqrt((mu + 2 * t)**2 + 4.0 * (delta * ks)**2)
        plot *= holoviews.Path((ks, ec), kdims=[dims.k, dims.E_t])(style={'linestyle':'--', 'color':'r'})
        plot *= holoviews.Path((ks, -ec), kdims=[dims.k, dims.E_t])(style={'linestyle':'--', 'color':'r'})
    return plot.relabel(title)

def find_pfaffian(H):
    return np.sign(np.real(pf.pfaffian(1j*H)))

In [42]:
def plot_wf(syst, wf1, wf2, lstyle='-', lcolor='b'):
    xs = np.array([i.pos[0] for i in syst.sites])
    indx = np.argsort(xs)
    wf_sq = np.linalg.norm(wf1.reshape(-1, 2), axis=1)**2 + np.linalg.norm(wf2.reshape(-1, 2), axis=1)**2
    plot = holoviews.Path((xs[indx], wf_sq[indx]), kdims=[dims.x, dims.amplitude])
    return plot(style={'linestyle': lstyle, 'color': lcolor},
                plot={'yticks': 0, 'xticks': list(range(0, len(xs), 10))})

def plot_pwave(L, t, delta, mu):
    # At mu=0 the first exited state is not well defined due to the massive degeneracy.
    # That is why we add a small offset to mu.
    syst = kitaev_chain(L).finalized()
    p = SimpleNamespace(t=t, delta=delta, mu=mu+1e-4)
    ham = syst.hamiltonian_submatrix(args=[p])
    ev, evec = np.linalg.eigh(ham)
    return (plot_wf(syst, evec[:, L], evec[:, L-1]) *
            plot_wf(syst, evec[:, L+1] , evec[:, L-2], lstyle='--', lcolor='r'))

syst = kitaev_chain(L=25)
mus = np.arange(0, 4, 0.2)
p = SimpleNamespace(t=1, delta=1, mu=mus)

(spectrum(syst, p, xticks=[0, 1, 2, 3], yticks=range(-3, 4), 
          xdim=dims.mu_t, ydim=dims.E_t, ylims=(-3, 3)) * 
 holoviews.HoloMap({mu: holoviews.VLine(mu) for mu in mus}, kdims=[dims.mu_t]) +
 holoviews.HoloMap({mu: plot_pwave(25, 1.0, 1.0, mu) for mu in mus}, kdims=[dims.mu_t]))

/home/thomas/anaconda2/envs/python3/lib/python3.6/site-packages/kwant/linalg/lll.py:103: FutureWarning: `rcond` parameter will change to the default of machine precision times ``max(M, N)`` where M and N are the input matrix dimensions.
To use the future default and silence this warning we advise to pass `rcond=None`, to keep using the old, explicitly pass `rcond=-1`.
  coefs = np.linalg.lstsq(vecs_orig.T, vecs.T)[0]
/home/thomas/anaconda2/envs/python3/lib/python3.6/site-packages/kwant/linalg/lll.py:144: FutureWarning: `rcond` parameter will change to the default of machine precision times ``max(M, N)`` where M and N are the input matrix dimensions.
To use the future default and silence this warning we advise to pass `rcond=None`, to keep using the old, explicitly pass `rcond=-1`.
  center_coords = np.array(np.round(np.linalg.lstsq(basis.T, vec)[0]), int)


:Layout
   .HoloMap.I  :HoloMap   [$\mu/t$]
      :Overlay
         .Path.I  :Path   [$\mu/t$,$E/t$]
         .VLine.I :VLine   [x,y]
   .HoloMap.II :HoloMap   [$\mu/t$]
      :Overlay
         .Path.I  :Path   [$x$,$|u|^2 + |v|^2$]
         .Path.II :Path   [$x$,$|u|^2 + |v|^2$]

## SSH Chain

In [39]:
import sys
sys.path.append('../code')
#from init_mooc_nb import *
#init_notebook()

%output size=150
dims = SimpleNamespace(E_t=holoviews.Dimension(r'$E/t$'),
                       mu_t=holoviews.Dimension(r'$\mu/t$'),
                       lambda_=holoviews.Dimension(r'$\lambda$'),
                       x=holoviews.Dimension(r'$x$'),
                       k=holoviews.Dimension(r'$k$'),
                       t2_mu=holoviews.Dimension(r'$t2/\mu$'),
                       amplitude=holoviews.Dimension(r'$|u|^2 + |v|^2$'))

holoviews.core.dimension.title_format = ''

def ssh_chain(L=None, periodic=False):
    lat = kwant.lattice.chain()

    if L is None:
        syst = kwant.Builder(kwant.TranslationalSymmetry((-1,)))
        L = 1
    else:
        syst = kwant.Builder()

    # transformation to antisymmetric basis
    U = np.array([[1.0, 1.0], [1.j, -1.j]]) / np.sqrt(2)

    def onsite(onsite, p): 
        return - p.mu
    
    for x in range(L):
        syst[lat(2*x)] = onsite
        syst[lat(2*x+1)] = 0

    def hop(site1, site2, p):
        if site1.pos[0]%2==0:
            hop_str = p.t1 
        else:
            #import pdb
            #pdb.set_trace()
            hop_str = p.t2
        
        return hop_str
            
    syst[kwant.HoppingKind((1,), lat)] = hop

    if periodic:
        def last_hop(site1, site2, p):
            return hop(site1, site2, p) 
        
        syst[lat(0), lat(L - 1)] = last_hop
    return syst


def bandstructure(mu,t1=1,t2=1, show_pf=False):
    syst = ssh_chain(None)
    p = SimpleNamespace(t1=t1,t2=t2, mu=mu)
    plot = holoviews.Overlay([spectrum(syst, p, ydim="$E/T$", xdim='$k$')][-4:4])
    h_1 = h_k(syst, p, 0)
    h_2 = h_k(syst, p, np.pi)
    pfaffians = [find_pfaffian(h_1), find_pfaffian(h_2)]
    
    if show_pf:
        signs = [('>' if pf > 0 else '<') for pf in pfaffians]
        title = "$\mu = {mu} t$, Pf$(iH_{{k=0}}) {sign1} 0$, Pf$(iH_{{k=\pi}}) {sign2} 0$"
        title = title.format(mu=mu, sign1=signs[0], sign2=signs[1])
        plot *= holoviews.VLine(0) * holoviews.VLine(-np.pi)
    else:
        if pfaffians[0] * pfaffians[1] < 0:
            title = "$\mu = {mu} t$, topological ".format(mu=mu)
        else:
            title = "$\mu = {mu} t$, trivial ".format(mu=mu)
        

    return plot.relabel(title)

def find_pfaffian(H):
    return np.sign(np.real(pf.pfaffian(1j*H)))

In [30]:
def plot_wf(syst, wf1, wf2, lstyle='-', lcolor='b'):
    xs = np.array([i.pos[0] for i in syst.sites])
    indx = np.argsort(xs)
    wf_sq = np.abs(wf1)**2 + np.abs(wf2)**2
    plot = holoviews.Path((xs[indx], wf_sq[indx]), kdims=[dims.x, dims.amplitude])
    return plot(style={'linestyle': lstyle, 'color': lcolor},
                plot={'yticks': 0, 'xticks': list(range(0, len(xs), 10))})

def plot_pwave(L, t1,t2,mu):
    # At mu=0 the first exited state is not well defined due to the massive degeneracy.
    # That is why we add a small offset to mu.
    syst = ssh_chain(L).finalized()
    p = SimpleNamespace(t1=t1,t2=t2, mu=mu+1e-4)
    ham = syst.hamiltonian_submatrix(args=[p])
    ev, evec = np.linalg.eigh(ham)
    return (plot_wf(syst, evec[:, L], evec[:, L-1]) *
            plot_wf(syst, evec[:, L+1] , evec[:, L-2], lstyle='--', lcolor='r'))

syst = ssh_chain(L=25)
t2s = np.arange(0, 4, 0.2)
p = SimpleNamespace(t1=1,t2=t2s, mu=0)

(spectrum(syst, p, xticks=[0, 1, 2, 3], yticks=range(-3, 4), 
          xdim=dims.t2_mu, ydim=dims.E_t, ylims=(-3, 3)) * 
holoviews.HoloMap({t2: holoviews.VLine(t2) for t2 in t2s}, kdims=[dims.t2_mu]) +\
 holoviews.HoloMap({t2: plot_pwave(25, 1.0, t2, 0.) for t2 in t2s}, kdims=[dims.t2_mu]))

/home/thomas/anaconda2/envs/python3/lib/python3.6/site-packages/kwant/linalg/lll.py:103: FutureWarning: `rcond` parameter will change to the default of machine precision times ``max(M, N)`` where M and N are the input matrix dimensions.
To use the future default and silence this warning we advise to pass `rcond=None`, to keep using the old, explicitly pass `rcond=-1`.
  coefs = np.linalg.lstsq(vecs_orig.T, vecs.T)[0]
/home/thomas/anaconda2/envs/python3/lib/python3.6/site-packages/kwant/linalg/lll.py:144: FutureWarning: `rcond` parameter will change to the default of machine precision times ``max(M, N)`` where M and N are the input matrix dimensions.
To use the future default and silence this warning we advise to pass `rcond=None`, to keep using the old, explicitly pass `rcond=-1`.
  center_coords = np.array(np.round(np.linalg.lstsq(basis.T, vec)[0]), int)


:Layout
   .HoloMap.I  :HoloMap   [$t2/\mu$]
      :Overlay
         .Path.I  :Path   [$t2/\mu$,$E/t$]
         .VLine.I :VLine   [x,y]
   .HoloMap.II :HoloMap   [$t2/\mu$]
      :Overlay
         .Path.I  :Path   [$x$,$|u|^2 + |v|^2$]
         .Path.II :Path   [$x$,$|u|^2 + |v|^2$]

We see that as $t_2$ is varied with fixed $t_1=1$ zero energy states exist at the edges of the SSH chain. This is a consequence of sublattice symmettry which induces positive, negative energy pairs for eigenvectors composed of cellA,cellB and cellA,-cellB. When $t_2<0$ states at the end of the chain are highly localized as they are unable to swap with the nearest neighbor due to large energy imbalance. The energy of these localized states must be made near to equal $t_1$ such that the energy levels may repel against those of the other lattice and mix the states. 

## Ruining sublattice symmetry 

Sublattice symmetry is a result of all degrees of freedom being between two groups, and not unique to two groups. We remove this symmettry by setting $\mu_1 \neq 0$ and observing a splitting of the energy spectrum away from $E=0$. 

In [40]:
def plot_wf(syst, wf1, wf2, lstyle='-', lcolor='b'):
    xs = np.array([i.pos[0] for i in syst.sites])
    indx = np.argsort(xs)
    wf_sq = np.abs(wf1)**2 + np.abs(wf2)**2
    plot = holoviews.Path((xs[indx], wf_sq[indx]), kdims=[dims.x, dims.amplitude])
    return plot(style={'linestyle': lstyle, 'color': lcolor},
                plot={'yticks': 0, 'xticks': list(range(0, len(xs), 10))})

def plot_pwave(L, t1,t2,mu):
    # At mu=0 the first exited state is not well defined due to the massive degeneracy.
    # That is why we add a small offset to mu.
    syst = ssh_chain(L).finalized()
    p = SimpleNamespace(t1=t1,t2=t2, mu=mu+1e-4)
    ham = syst.hamiltonian_submatrix(args=[p])
    ev, evec = np.linalg.eigh(ham)
    return (plot_wf(syst, evec[:, L], evec[:, L-1]) *
            plot_wf(syst, evec[:, L+1] , evec[:, L-2], lstyle='--', lcolor='r'))

syst = ssh_chain(L=25)
t2s = np.arange(0, 4, 0.2)
p = SimpleNamespace(t1=1,t2=t2s, mu=0.1)

(spectrum(syst, p, xticks=[0, 1, 2, 3], yticks=range(-3, 4), 
          xdim=dims.t2_mu, ydim=dims.E_t, ylims=(-3, 3)) * 
holoviews.HoloMap({t2: holoviews.VLine(t2) for t2 in t2s}, kdims=[dims.t2_mu]) +\
 holoviews.HoloMap({t2: plot_pwave(25, 1.0, t2, 0.1) for t2 in t2s}, kdims=[dims.t2_mu]))

/home/thomas/anaconda2/envs/python3/lib/python3.6/site-packages/kwant/linalg/lll.py:103: FutureWarning: `rcond` parameter will change to the default of machine precision times ``max(M, N)`` where M and N are the input matrix dimensions.
To use the future default and silence this warning we advise to pass `rcond=None`, to keep using the old, explicitly pass `rcond=-1`.
  coefs = np.linalg.lstsq(vecs_orig.T, vecs.T)[0]
/home/thomas/anaconda2/envs/python3/lib/python3.6/site-packages/kwant/linalg/lll.py:144: FutureWarning: `rcond` parameter will change to the default of machine precision times ``max(M, N)`` where M and N are the input matrix dimensions.
To use the future default and silence this warning we advise to pass `rcond=None`, to keep using the old, explicitly pass `rcond=-1`.
  center_coords = np.array(np.round(np.linalg.lstsq(basis.T, vec)[0]), int)


:Layout
   .HoloMap.I  :HoloMap   [$t2/\mu$]
      :Overlay
         .Path.I  :Path   [$t2/\mu$,$E/t$]
         .VLine.I :VLine   [x,y]
   .HoloMap.II :HoloMap   [$t2/\mu$]
      :Overlay
         .Path.I  :Path   [$x$,$|u|^2 + |v|^2$]
         .Path.II :Path   [$x$,$|u|^2 + |v|^2$]